In [1]:
import warnings

warnings.filterwarnings(
    "ignore",
    message="torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.",
)

warnings.filterwarnings(
    "ignore",
    message="torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.",
)

In [2]:
# Written by Yukang Chen
# Some code based on https://github.com/epfml/landmark-attention
#
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
#     http://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

from tqdm.notebook import tqdm

import sys
import io
import os
import copy
import json
import math
import logging
import pandas as pd
from dataclasses import dataclass, field
from typing import Dict, Optional, Sequence

import torch
import transformers
from torch.utils.data import Dataset
from transformers import Trainer, DataCollatorForLanguageModeling
from llama_attn_replace_sft import replace_llama_attn
from gptneox_attn_replace import replace_gpt_neox_attn
from peft import LoraConfig, get_peft_model
from torch.distributed import barrier

IGNORE_INDEX = -100
DEFAULT_PAD_TOKEN = "[PAD]"
DEFAULT_EOS_TOKEN = "</s>"
DEFAULT_BOS_TOKEN = "<s>"
DEFAULT_UNK_TOKEN = "<unk>"

def _make_r_io_base(f, mode: str):
    if not isinstance(f, io.IOBase):
        f = open(f, mode=mode)
    return f

def jload(f, mode="r"):
    """Load a .json file into a dictionary."""
    f = _make_r_io_base(f, mode)
    jdict = json.load(f)
    f.close()
    return jdict

PROMPT_DICT = {
    "prompt_input": (
        "Below is an instruction that describes a task, paired with an input that provides further context. "
        "Write a response that appropriately completes the request.\n\n"
        "### Instruction:\n{instruction}\n\n### Input:\n{input}\n\n### Response:"
    ),
    "prompt_no_input": (
        "Below is an instruction that describes a task. "
        "Write a response that appropriately completes the request.\n\n"
        "### Instruction:\n{instruction}\n\n### Response:"
    ),
    "prompt_no_input_llama2":(
        "[INST] <<SYS>>\n"
        "You are a helpful, respectful and honest assistant. Always answer as helpfully as possible, while being safe.  Your answers should not include any harmful, unethical, racist, sexist, toxic, dangerous, or illegal content. Please ensure that your responses are socially unbiased and positive in nature.\n\n"
        "If a question does not make any sense, or is not factually coherent, explain why instead of answering something not correct. If you don't know the answer to a question, please don't share false information.\n"
        "<</SYS>> \n\n {instruction} [/INST]"
    ),
    "prompt_input_llama2": (
        "[INST] <<SYS>>\n"
        "You are a helpful, respectful and honest assistant. Always answer as helpfully as possible, while being safe.  Your answers should not include any harmful, unethical, racist, sexist, toxic, dangerous, or illegal content. Please ensure that your responses are socially unbiased and positive in nature.\n\n"
        "If a question does not make any sense, or is not factually coherent, explain why instead of answering something not correct. If you don't know the answer to a question, please don't share false information.\n"
        "<</SYS>> \n\n {instruction} \n{input} [/INST]"
    ),
    "prompt_llama2": "[INST]{instruction}[/INST]",
    "prompt_input_diploma_special":(
        "Below is an instruction that describes a task, paired with an input that provides further context. "
        "Write a response that appropriately completes the request.\n\n"
        "### Instruction:\nBelow is a diploma text. Your task is to generate abstract of this diploma.\n\n### Input:\n{input}\n\n"
    ),
}


@dataclass
class ModelArguments:
    model_name_or_path: Optional[str] = field(default="EleutherAI/pythia-1.4b-deduped")
    model_type: Optional[str] = field(default="llama")


@dataclass
class DataArguments:
    train_data_path: str = field(default=None, metadata={"help": "Path to the training data."})
    val_data_path: str = field(default=None, metadata={"help": "Path to the validation data."})
    nrows: int = 1
    diploma_prefix_len: int = 1


@dataclass
class TrainingArguments(transformers.TrainingArguments):
    cache_dir: Optional[str] = field(default=None)
    optim: str = field(default="adamw_torch")
    model_max_length: int = field(
        default=8192 * 4,
        metadata={"help": "Maximum sequence length. Sequences will be right padded (and possibly truncated)."},
    )
    use_flash_attn: bool = field(
        default=True,
        metadata={"help": "Whether use flash attention for training."},
    )
    use_full_attn: bool = field(
        default=False,
        metadata={"help": "Whether to use plain, full-attention for training."},
    )
    low_rank_training: bool = field(
        default=True,
        metadata={"help": "Whether use low rank adaptation for training."},
    )
    trainable_params: str = field(
        default="embed,norm",
        metadata={"help": "Additional trainable parameters except LoRA weights, if low rank training."},
    )

def smart_tokenizer_and_embedding_resize(
    special_tokens_dict: Dict,
    tokenizer: transformers.PreTrainedTokenizer,
    model: transformers.PreTrainedModel,
):
    """Resize tokenizer and embedding.

    Note: This is the unoptimized version that may make your embedding size not be divisible by 64.
    """
    num_new_tokens = tokenizer.add_special_tokens(special_tokens_dict)
    model.resize_token_embeddings(len(tokenizer))

    if num_new_tokens > 0:
        input_embeddings = model.get_input_embeddings().weight.data
        output_embeddings = model.get_output_embeddings().weight.data

        input_embeddings_avg = input_embeddings[:-num_new_tokens].mean(dim=0, keepdim=True)
        output_embeddings_avg = output_embeddings[:-num_new_tokens].mean(dim=0, keepdim=True)

        input_embeddings[-num_new_tokens:] = input_embeddings_avg
        output_embeddings[-num_new_tokens:] = output_embeddings_avg


def _tokenize_fn(strings: Sequence[str], tokenizer: transformers.PreTrainedTokenizer) -> Dict:
    """Tokenize a list of strings."""
    tokenized_list = []
    for text in tqdm(strings, desc="Texts..."):
        tokenized_list.append(tokenizer(
            text,
            return_tensors="pt",
            padding="longest",
            max_length=tokenizer.model_max_length,
            truncation=True,
        ))
    input_ids = labels = [tokenized.input_ids[0] for tokenized in tokenized_list]
    input_ids_lens = labels_lens = [
        tokenized.input_ids.ne(tokenizer.pad_token_id).sum().item() for tokenized in tokenized_list
    ]
    return dict(
        input_ids=input_ids,
        labels=labels,
        input_ids_lens=input_ids_lens,
        labels_lens=labels_lens,
    )


def preprocess(
    sources: Sequence[str],
    targets: Sequence[str],
    tokenizer: transformers.PreTrainedTokenizer,
) -> Dict:
    """Preprocess the data by tokenizing."""
    examples = [s + t for s, t in zip(sources, targets)]
    targets_tokenized = _tokenize_fn(targets, tokenizer)
    examples_tokenized = _tokenize_fn(examples, tokenizer)
    input_ids = [] 
    for example_input_id, target_input_id, example_len, target_len in zip(examples_tokenized["input_ids"], targets_tokenized["input_ids"], examples_tokenized["input_ids_lens"], targets_tokenized["input_ids_lens"]):
        limit = tokenizer.model_max_length
        res = example_input_id
        if example_len == limit:
            res = example_input_id.tolist()[:-target_len] + target_input_id.tolist()[:target_len]
        input_id = torch.tensor(res, dtype=torch.int)
        input_id = input_id.type(torch.LongTensor)
        input_ids.append(input_id)
    labels = copy.deepcopy(input_ids)
    for label, example_len, target_len in zip(labels, examples_tokenized["input_ids_lens"], targets_tokenized["input_ids_lens"]):
        ignore_end = example_len - target_len
        label[:ignore_end] = IGNORE_INDEX
    return dict(input_ids=input_ids, labels=labels)


class SupervisedDataset(Dataset):
    """Dataset for supervised fine-tuning."""

    def __init__(self, data_path: str, tokenizer: transformers.PreTrainedTokenizer, nrows: int, diploma_prefix_len: int):
        super(SupervisedDataset, self).__init__()
        logging.warning("Loading data...")
        data_table = pd.read_csv(data_path)
        if nrows is not None:
            data_table = data_table.sample(min(len(data_table), nrows))
        else:
            data_table = data_table.sample(frac=1)

        logging.warning("Formatting inputs...")

        prompt_input_diploma = PROMPT_DICT["prompt_input_diploma_special"]
        sources = [
            prompt_input_diploma.format(input=diploma[:diploma_prefix_len])
            for diploma in data_table["diploma"]
        ]

        targets = [f"### Response:{abstract}{tokenizer.eos_token}" for abstract in data_table["abstract"]]

        logging.warning("Tokenizing inputs... This may take some time...")
        data_dict = preprocess(sources, targets, tokenizer)

        self.input_ids = data_dict["input_ids"]
        self.labels = data_dict["labels"]

    def __len__(self):
        return len(self.input_ids)

    def __getitem__(self, i) -> Dict[str, torch.Tensor]:
        return dict(input_ids=self.input_ids[i], labels=self.labels[i])


@dataclass
class DataCollatorForSupervisedDataset(object):
    """Collate examples for supervised fine-tuning."""

    tokenizer: transformers.PreTrainedTokenizer

    def __call__(self, instances: Sequence[Dict]) -> Dict[str, torch.Tensor]:
        input_ids, labels = tuple([instance[key] for instance in instances] for key in ("input_ids", "labels"))
        input_ids = torch.nn.utils.rnn.pad_sequence(
            input_ids, batch_first=True, padding_value=self.tokenizer.pad_token_id
        )
        labels = torch.nn.utils.rnn.pad_sequence(labels, batch_first=True, padding_value=IGNORE_INDEX)
        return dict(
            input_ids=input_ids,
            labels=labels,
            attention_mask=input_ids.ne(self.tokenizer.pad_token_id),
        )


def make_supervised_data_module(tokenizer: transformers.PreTrainedTokenizer, data_args) -> Dict:
    """Make dataset and collator for supervised fine-tuning."""
    train_dataset = SupervisedDataset(tokenizer=tokenizer, data_path=data_args.train_data_path, nrows=data_args.nrows, diploma_prefix_len=data_args.diploma_prefix_len)
    val_dataset = SupervisedDataset(tokenizer=tokenizer, data_path=data_args.val_data_path, nrows=data_args.nrows, diploma_prefix_len=data_args.diploma_prefix_len)
    data_collator = DataCollatorForSupervisedDataset(tokenizer=tokenizer)
    return dict(train_dataset=train_dataset, eval_dataset=val_dataset, data_collator=data_collator)


def train(model_args, data_args, training_args):
    print("Begin train")
    
    print("Parsed arguments")

    # NOTE: May expand supported model types in the future
    if model_args.model_type == "gpt-neox":
        replace_gpt_neox_attn(training_args.use_flash_attn, training_args.use_full_attn)
    else:
        replace_llama_attn(training_args.use_flash_attn, training_args.use_full_attn)

    # Set RoPE scaling factor
    config = transformers.AutoConfig.from_pretrained(
        model_args.model_name_or_path,
        cache_dir=training_args.cache_dir,
    )

    orig_rope_scaling = getattr(config, "rope_scaling", None)
    if orig_rope_scaling is None:
        orig_rope_scaling = {"factor": 1}
    orig_rope_scaling_factor = orig_rope_scaling["factor"] if "factor" in orig_rope_scaling.keys() else 1
    orig_ctx_len = getattr(config, "max_position_embeddings", None)
    if orig_ctx_len:
        orig_ctx_len *= orig_rope_scaling_factor
        if training_args.model_max_length > orig_ctx_len:
            scaling_factor = float(math.ceil(training_args.model_max_length / orig_ctx_len))
            config.rope_scaling = {"type": "linear", "factor": scaling_factor}
            
    print("Created config")

    # Load model and tokenizer
    model = transformers.AutoModelForCausalLM.from_pretrained(
        model_args.model_name_or_path,
        config=config,
        cache_dir=training_args.cache_dir,
        torch_dtype=torch.bfloat16,
    )
    
    print("Loaded model")

    tokenizer = transformers.AutoTokenizer.from_pretrained(
        model_args.model_name_or_path,
        cache_dir=training_args.cache_dir,
        model_max_length=training_args.model_max_length,
        padding_side="right",
        use_fast=True,
    )
    
    print("Loaded tokenizer")

    special_tokens_dict = dict()
    if tokenizer.pad_token is None:
        special_tokens_dict["pad_token"] = DEFAULT_PAD_TOKEN
    if tokenizer.eos_token is None:
        special_tokens_dict["eos_token"] = DEFAULT_EOS_TOKEN
    if tokenizer.bos_token is None:
        special_tokens_dict["bos_token"] = DEFAULT_BOS_TOKEN
    if tokenizer.unk_token is None:
        special_tokens_dict["unk_token"] = DEFAULT_UNK_TOKEN

    smart_tokenizer_and_embedding_resize(
        special_tokens_dict=special_tokens_dict,
        tokenizer=tokenizer,
        model=model,
    )

    data_module = make_supervised_data_module(tokenizer=tokenizer, data_args=data_args)
    
    print("Created data_module")

    if training_args.low_rank_training:
        if model_args.model_type == "gpt-neox":
            # added `dense` to match with llama as the basic LoRA would only target 'query_key_value'
            targets = ["query_key_value", "dense"]
        else:
            targets=["q_proj", "k_proj", "v_proj", "o_proj"]

        config = LoraConfig(
            r=8,
            lora_alpha=16,
            target_modules=targets,
            lora_dropout=0,
            bias="none",
            task_type="CAUSAL_LM",
        )
        model = get_peft_model(model, config)
        # enable trainable params
        [p.requires_grad_() for n, p in model.named_parameters() if any([k in n for k in training_args.trainable_params.split(",")])]

    model.config.use_cache = False         # required for gradient checkpointing
    model.enable_input_require_grads()     # required for gradient checkpointing
    model.gradient_checkpointing_enable()  # enable gradient checkpointing
    
    print("Prepared model to learn")

    trainer = Trainer(model=model, tokenizer=tokenizer, args=training_args, **data_module)
    trainer.train()
    trainer.save_state()
    trainer.save_model(output_dir=training_args.output_dir)
    
    print("Learnt model")

2024-05-18 09:59:18.805929: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [3]:
import os
from huggingface_hub import login
login(os.environ['hf-read-token'])

Token will not been saved to git credential helper. Pass `add_to_git_credential=True` if you want to set the git credential as well.
Token is valid (permission: read).
Your token has been saved to /tmp/xdg_cache/huggingface/token
Login successful


In [4]:
from pathlib import Path
CACHE_DIR = Path("../cache/")
DATASET_DIR = Path("/home/jupyter/mnt/datasets/spbu_diplomas/russian_dataset/")
OUTPUT_DIR = Path("./llama_replaced_attn_8k_without_checkpoints_new_tokenize_attempt_3_output_dir/")
LOGGING_DIR = Path("./llama_replaced_attn_8k_without_checkpoints_new_tokenize_attempt_3_logging_dir/")
MODEL_MAX_LENGTH = 8192
INF = int(1e7)

In [6]:
model_args = ModelArguments(
    model_name_or_path="meta-llama/Llama-2-7b-hf",
)


data_args = DataArguments(
    train_data_path=DATASET_DIR.joinpath("russian_dataset_train.csv").as_posix(),
    val_data_path=DATASET_DIR.joinpath("russian_dataset_val.csv").as_posix(),
    nrows=None, # 720 * 3,
    diploma_prefix_len=INF,
)

training_args = TrainingArguments(
    bf16=True,
    output_dir=OUTPUT_DIR.as_posix(),
    model_max_length=MODEL_MAX_LENGTH,
    use_flash_attn=True,
    low_rank_training=True,
    num_train_epochs=3,
    per_device_train_batch_size=1,
    per_device_eval_batch_size=2,
    gradient_accumulation_steps=8,
    evaluation_strategy="no",
    # eval_steps=1,
    learning_rate=2e-5,
    weight_decay=0.0,
    warmup_steps=20,
    lr_scheduler_type="constant_with_warmup",
    logging_steps=1,
    logging_dir=LOGGING_DIR.as_posix(),
    deepspeed="ds_configs/stage2.json",
    tf32=True,
    cache_dir=CACHE_DIR.as_posix(),
    report_to=['tensorboard'],
    save_strategy="no",
)
training_args

TrainingArguments(output_dir='llama_replaced_attn_8k_without_checkpoints_new_tokenize_attempt_3_output_dir', overwrite_output_dir=False, do_train=False, do_eval=False, do_predict=False, evaluation_strategy=<IntervalStrategy.NO: 'no'>, prediction_loss_only=False, per_device_train_batch_size=1, per_device_eval_batch_size=2, per_gpu_train_batch_size=None, per_gpu_eval_batch_size=None, gradient_accumulation_steps=8, eval_accumulation_steps=None, eval_delay=0, learning_rate=2e-05, weight_decay=0.0, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=3, max_steps=-1, lr_scheduler_type=<SchedulerType.CONSTANT_WITH_WARMUP: 'constant_with_warmup'>, warmup_ratio=0.0, warmup_steps=20, log_level='passive', log_level_replica='warning', log_on_each_node=True, logging_dir='llama_replaced_attn_8k_without_checkpoints_new_tokenize_attempt_3_logging_dir', logging_strategy=<IntervalStrategy.STEPS: 'steps'>, logging_first_step=False, logging_steps=1, logging_nan_inf_fi

In [7]:
print("Begin train")

print("Parsed arguments")

# NOTE: May expand supported model types in the future
if model_args.model_type == "gpt-neox":
    replace_gpt_neox_attn(training_args.use_flash_attn, training_args.use_full_attn)
else:
    replace_llama_attn(training_args.use_flash_attn, training_args.use_full_attn)

# Set RoPE scaling factor
config = transformers.AutoConfig.from_pretrained(
    model_args.model_name_or_path,
    cache_dir=training_args.cache_dir,
)

orig_rope_scaling = getattr(config, "rope_scaling", None)
if orig_rope_scaling is None:
    orig_rope_scaling = {"factor": 1}
orig_rope_scaling_factor = orig_rope_scaling["factor"] if "factor" in orig_rope_scaling.keys() else 1
orig_ctx_len = getattr(config, "max_position_embeddings", None)
if orig_ctx_len:
    orig_ctx_len *= orig_rope_scaling_factor
    if training_args.model_max_length > orig_ctx_len:
        scaling_factor = float(math.ceil(training_args.model_max_length / orig_ctx_len))
        config.rope_scaling = {"type": "linear", "factor": scaling_factor}

print("Created config")

# Load model and tokenizer
model = transformers.AutoModelForCausalLM.from_pretrained(
    model_args.model_name_or_path,
    config=config,
    cache_dir=training_args.cache_dir,
    torch_dtype=torch.bfloat16,
)

print("Loaded model")

tokenizer = transformers.AutoTokenizer.from_pretrained(
    model_args.model_name_or_path,
    cache_dir=training_args.cache_dir,
    model_max_length=training_args.model_max_length,
    padding_side="right",
    use_fast=True,
)

print("Loaded tokenizer")

special_tokens_dict = dict()
if tokenizer.pad_token is None:
    special_tokens_dict["pad_token"] = DEFAULT_PAD_TOKEN
if tokenizer.eos_token is None:
    special_tokens_dict["eos_token"] = DEFAULT_EOS_TOKEN
if tokenizer.bos_token is None:
    special_tokens_dict["bos_token"] = DEFAULT_BOS_TOKEN
if tokenizer.unk_token is None:
    special_tokens_dict["unk_token"] = DEFAULT_UNK_TOKEN

smart_tokenizer_and_embedding_resize(
    special_tokens_dict=special_tokens_dict,
    tokenizer=tokenizer,
    model=model,
)

Begin train
Parsed arguments
Created config


Loading checkpoint shards: 100%|██████████| 2/2 [02:05<00:00, 62.54s/it]

Loaded model


Loaded tokenizer

Using pad_token, but it is not set yet.


In [8]:
data_module = make_supervised_data_module(tokenizer=tokenizer, data_args=data_args)

print("Created data_module")

if training_args.low_rank_training:
    if model_args.model_type == "gpt-neox":
        # added `dense` to match with llama as the basic LoRA would only target 'query_key_value'
        targets = ["query_key_value", "dense"]
    else:
        targets=["q_proj", "k_proj", "v_proj", "o_proj"]

    config = LoraConfig(
        r=4,
        lora_alpha=16,
        target_modules=targets,
        lora_dropout=0,
        bias="none",
        task_type="CAUSAL_LM",
    )
    model = get_peft_model(model, config)
    # enable trainable params
    [p.requires_grad_() for n, p in model.named_parameters() if any([k in n for k in training_args.trainable_params.split(",")])]

model.config.use_cache = False         # required for gradient checkpointing
model.enable_input_require_grads()     # required for gradient checkpointing
model.gradient_checkpointing_enable()  # enable gradient checkpointing

print("Prepared model to learn")

Texts...:   0%|          | 0/7623 [00:00<?, ?it/s]

Texts...:   0%|          | 0/7623 [00:00<?, ?it/s]

<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input_id = torch.tensor(res, dtype=torch.int)
<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input_id = torch.tensor(res, dtype=torch.int)
<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input_id = torch.tensor(res, dtype=torch.int)
<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone()

Texts...:   0%|          | 0/1397 [00:00<?, ?it/s]

Texts...:   0%|          | 0/1397 [00:00<?, ?it/s]

<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input_id = torch.tensor(res, dtype=torch.int)
<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input_id = torch.tensor(res, dtype=torch.int)
<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input_id = torch.tensor(res, dtype=torch.int)
<ipython-input-2-1fbf6446dfbb>:188: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone()

Created data_module
Prepared model to learn


### Example of new tokenization

In [94]:
tokenizer.decode(data_module["train_dataset"][0]["input_ids"])

'<s> Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.\n\n### Instruction:\nBelow is a diploma text. Your task is to generate abstract of this diploma.\n\n### Input:\nСАНКТ-ПЕТЕРБУРГСКИЙ\nГОСУДАРСТВЕННЫЙ УНИВЕРСИТЕТ\nФизический факультет\nКафедра Статистической физики\n\nУравнения стохастической динамики в\nокрестности λ-точки\nВыпускная квалификационная работа студента 406\nгруппы\nЖаворонкова Юрия Александровича\n\nНаучный руководитель:\nд.ф. - м.н., профессор Налимов М.Ю.\nРецензент:\nд.ф. - м.н., профессор Антонов Н.В.\n\nСанкт-Петербург\n2017 г.\n\n\x0cСодержание\n1 Введение\n\n2\n\n2 Модель F стохастической динамики\n\n3\n\n3 Модификация модели\n\n5\n\n4 Заключение\n\n12\n\nСписок литературы\n\n13\n\n1\n\n\x0c1\n\nВведение\n\nНастоящая работа посвящена изучению явления Бозе-конденсации. Актуальность данного направления исследования подтверждается многочисленными работами ка

### Continue training

In [ ]:
import numpy as np

check = []
lens = []
for x in data_module["train_dataset"]:
    check.append(list(set(x["labels"].tolist())).__len__() == 1)
    lens.append(x["input_ids"].ne(tokenizer.pad_token_id).sum())
np.mean(check), np.mean(lens)

In [9]:
trainer = Trainer(model=model, tokenizer=tokenizer, args=training_args, **data_module)
trainer.train()
trainer.save_state()
trainer.save_model(output_dir=training_args.output_dir)

print("Learnt model")

/home/jupyter/.local/lib/python3.10/site-packages/accelerate/accelerator.py:446: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None)
  warnings.warn(


[2024-05-18 11:28:26,517] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)
 [WARNING]  async_io requires the dev libaio .so object and headers but these were not found.
 [WARNING]  async_io: please install the libaio-dev package with apt
 [WARNING]  If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.
 [WARNING]  Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH
 [WARNING]  sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.3
 [WARNING]  using untested triton version (2.3.0), only 1.0.0 is known to be compatible


  0%|          | 1/2856 [00:20<16:22:10, 20.64s/it]

{'loss': 2.9548, 'learning_rate': 1.0000000000000002e-06, 'epoch': 0.0}


  0%|          | 2/2856 [00:38<15:07:48, 19.08s/it]

...

  9%|▉         | 271/2856 [1:21:03<12:54:02, 17.97s/it]

{'loss': 1.4794, 'learning_rate': 2e-05, 'epoch': 0.28}


 10%|▉         | 272/2856 [1:21:21<12:53:50, 17.97s/it]

{'loss': 1.4069, 'learning_rate': 2e-05, 'epoch': 0.29}


KeyboardInterrupt: 

In [11]:
import os
from huggingface_hub import login
login(os.environ['hf-write-token'])
model_id = "nvdenisov2002/llama-longLoRA-v5-8k-all-samples-3-epochs"
model.push_to_hub(model_id)

Token will not been saved to git credential helper. Pass `add_to_git_credential=True` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /tmp/xdg_cache/huggingface/token
Login successful


/home/jupyter/.local/lib/python3.10/site-packages/peft/utils/save_and_load.py:168: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(

adapter_model.bin:   0%|          | 0.00/533M [00:00<?, ?B/s]
adapter_model.bin:   0%|          | 8.19k/533M [00:00<3:34:54, 41.3kB/s]
adapter_model.bin:   0%|          | 328k/533M [00:00<07:25, 1.19MB/s]   
adapter_model.bin:   1%|          | 3.01M/533M [00:00<00:58, 8.98MB/s]
adapter_model.bin:   1%|          | 4.55M/533M [00:00<00:52, 10.1MB/s]
adapter_model.bin:   1%|          | 6.48M/533M [00:00<00:45, 11.6MB/s]
adapter_model.bin:   1%|▏         | 7.89M/533M [00:00<00:53, 9.73MB/s]
adapter_model.bin:   2%|▏         | 12.6M/533M [00:01<00:29, 17.8MB/s]
adapter_model.bin:   3%|▎         | 16.0M/533M [00:01<00:43, 11.8MB/s]
adapter_model.bin:   5%|▍         | 24.1M/533M [00:01<00:25, 20.2MB/s]
adapter_model.bin:   5%|▌         | 27.1M/533M [00:02<00:36, 13.9MB/s]
adapter_m

CommitInfo(commit_url='https://huggingface.co/nvdenisov2002/llama-longLoRA-v5-8k-all-samples-3-epochs/commit/83f0033350c63e1ec4a388387e27fccbfe17c0ac', commit_message='Upload model', commit_description='', oid='83f0033350c63e1ec4a388387e27fccbfe17c0ac', pr_url=None, pr_revision=None, pr_num=None)

### Try to inference model

In [21]:
input_ids = tokenizer("a cat sat on a")["input_ids"]
input_ids = torch.tensor(input_ids, dtype=torch.int).reshape((1, -1)).to('cuda')
input_ids

tensor([[   1,  263, 6635, 3290,  373,  263]], device='cuda:0',
       dtype=torch.int32)

In [ ]:
print("kek")

In [ ]:
generated = model.generate(input_ids=input_ids)

/home/jupyter/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:91: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:91: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:91: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:91: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:91: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:91: UserWarning: None of the inputs hav

In [ ]:
tokenizer.decode(generated)

### Interrupt because of bad tokenizing

In [9]:
trainer = Trainer(model=model, tokenizer=tokenizer, args=training_args, **data_module)
trainer.train()
trainer.save_state()
trainer.save_model(output_dir=training_args.output_dir)

print("Learnt model")

/home/jupyter/.local/lib/python3.10/site-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None)
  warnings.warn(


[2024-05-10 03:40:40,924] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)
 [WARNING]  async_io requires the dev libaio .so object and headers but these were not found.
 [WARNING]  async_io: please install the libaio-dev package with apt
 [WARNING]  If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.
 [WARNING]  Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH
 [WARNING]  sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.3
 [WARNING]  using untested triton version (2.3.0), only 1.0.0 is known to be compatible


  0%|          | 1/1350 [00:34<13:02:07, 34.79s/it]

{'loss': 27.1375, 'learning_rate': 1.0000000000000002e-06, 'epoch': 0.0}


  0%|          | 2/1350 [01:10<13:15:38, 35.41s/it]

...

  1%|          | 7/1350 [04:09<13:21:55, 35.83s/it]

{'loss': 24.0691, 'learning_rate': 7e-06, 'epoch': 0.03}


  1%|          | 8/1350 [04:45<13:17:50, 35.67s/it]

{'loss': 59.9522, 'learning_rate': 8.000000000000001e-06, 'epoch': 0.03}


KeyboardInterrupt: 

In [ ]:
from huggingface_hub import login
login("")
model_id = "nvdenisov2002/llama-longLoRA-v3-16k-2160-samples"
model.push_to_hub(model_id)

### Fail to save checkpoint

In [43]:
trainer = Trainer(model=model, tokenizer=tokenizer, args=training_args, **data_module)
trainer.train()
trainer.save_state()
trainer.save_model(output_dir=training_args.output_dir)

print("Learnt model")


                                                    it]
 18%|█▊        | 248/1350 [2:26:44<10:56:37, 35.75s/it]

{'loss': 0.0, 'learning_rate': 2e-05, 'epoch': 0.92}



                                                    it]
 18%|█▊        | 249/1350 [2:27:20<10:56:48, 35.79s/it]

{'loss': 0.0, 'learning_rate': 2e-05, 'epoch': 0.92}



                                                    it]
 19%|█▊        | 250/1350 [2:27:56<10:56:48, 35.83s/it]

...

{'loss': 3.5492, 'learning_rate': 2e-05, 'epoch': 1.85}



                                                    t]
 37%|███▋      | 500/1350 [4:55:48<8:20:23, 35.32s/it]

{'loss': 0.0, 'learning_rate': 2e-05, 'epoch': 1.85}


/home/jupyter/.local/lib/python3.10/site-packages/peft/utils/other.py:581: UserWarning: Unable to fetch remote file due to the following error (ProtocolError('Connection aborted.', RemoteDisconnected('Remote end closed connection without response')), '(Request ID: bc1f437f-0ece-4078-83a1-9a8a918848ad)') - silently ignoring the lookup for the file config.json in meta-llama/Llama-2-7b-hf.
  warnings.warn(
/home/jupyter/.local/lib/python3.10/site-packages/peft/utils/save_and_load.py:154: UserWarning: Could not find a config file in meta-llama/Llama-2-7b-hf - will assume that the vocabulary was not modified.
  warnings.warn(


AttributeError: 'LlamaForCausalLM' object has no attribute 'save_checkpoint'

In [ ]:
print("kek")

In [ ]:
model

In [ ]:
from huggingface_hub import notebook_login
notebook_login()

In [ ]:
model_id = "nvdenisov2002/llama-longLoRA-v3-16k"
model.push_to_hub(model_id)

### Unlucky try

In [28]:
train(model_args, data_args, training_args)

Begin train
Parsed arguments
Created config


Loading checkpoint shards: 100%|██████████| 2/2 [03:39<00:00, 109.68s/it]

Loaded model



Using pad_token, but it is not set yet.


Loaded tokenizer


Created data_module
Prepared model to learn


/home/jupyter/.local/lib/python3.10/site-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None)
  warnings.warn(


AttributeError: module 'wandb.proto.wandb_internal_pb2' has no attribute 'Result'